In [1]:
import nltk
import re
import numpy as np
from nltk.corpus import stopwords



In [2]:
import datasets

# Load the dataset
dataset = datasets.load_dataset("GEM/xlsum", "arabic")

# Print the dataset info
print(dataset)

Found cached dataset xlsum (C:/Users/DELL/.cache/huggingface/datasets/GEM___xlsum/arabic/2.0.0/eb0c1bd988fe61962620fe73722ebc91e0fd5729b4c8acbf3e3b3c50f8b22a96)


  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 37519
    })
    test: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 4689
    })
    validation: Dataset({
        features: ['gem_id', 'url', 'title', 'target', 'references', 'text'],
        num_rows: 4689
    })
})


### Discover how the dataset looks like

In [3]:
for i in range(5):
    print(dataset["train"][i])

{'gem_id': 'xlsum_arabic-train-1', 'url': 'https://www.bbc.com/arabic/worldnews/2014/03/140323_russian_troops_crimea_naval_base', 'title': 'القوات الأوكرانية تبدأ الانسحاب من القرم', 'target': 'بدأت القوات الأوكرانية الانسحاب من شبه جزيرة القرم. \n\n', 'references': ['بدأت القوات الأوكرانية الانسحاب من شبه جزيرة القرم. \n\n'], 'text': 'وكان الرئيس الأوكراني المؤقت، الكسندر تورتشينوف، قد أمر بسحب جميع القوات الأوكرانية من القرم.\n\nوسيطرت قوات روسية صباح الاثنين على قاعدة بحرية أوكرانية في فيودوسيا، في ثالث هجوم من نوعه خلال 48 ساعة، وذلك بحسب تصريحات مسؤولين أوكرانيين لبي بي سي .\n\nوقال المتحدث باسم وزارة الدفاع الأوكرانية فلاديسلاف سيليزنيوف إن القوات الروسية هاجمت القاعدة وألقت القبض على الجنود الأوكرانيين في قاعدة فيودوسيا وقيدت أيادي ضباطهم.\n\nومن المتوقع أن تسيطر الأزمة الأوكرانية على قمة مجموعة الدول الصناعية السبع في لاهاي.\n\nمواضيع قد تهمك نهاية\n\nوأكد الرئيس الأمريكي باراك أوباما خلال لقاء مع نظيره الصيني شى جين بينغ على أن "واشنطن وبكين يمكنهما، بالعمل سويا، تعزيز القانون

In [4]:
import pandas as pd

### From the above, we are interested in the 'text' and 'target' tags

In [5]:
train_inputs = dataset['train']['text']
train_labels = dataset['train']['target']


In [6]:
train_inputs = pd.DataFrame(train_inputs)
train_labels = pd.DataFrame(train_labels)
# Print the shape of the inputs and labels
print("Train inputs shape:", train_inputs.shape)
print("Train labels shape:", train_labels.shape)

Train inputs shape: (37519, 1)
Train labels shape: (37519, 1)


## Text Cleaning

### Analyze text by checking if it has any punctuation symbols

In [7]:
punctuations= ['?',':','!','.',',',';','؟','؛','،','(',')','/','"','-','\\', '\n', '#','*']

# Function to count occurrences of punctuations in a given sentence
def count_punctuations(sentence):
    return sum([sentence.count(p) for p in punctuations])

# Add new column with punctuation counts for each sentence
train_inputs['Punctuation_Counts_before'] = train_inputs[0].apply(count_punctuations)
train_labels['Punctuation_Counts_before'] = train_labels[0].apply(count_punctuations)

# Calculate total punctuation count for all sentences in DataFrame
total_punctuation_count_train = train_inputs['Punctuation_Counts_before'].sum()
total_punctuation_count_label = train_labels['Punctuation_Counts_before'].sum()


# Print total punctuation count
print(f'Total Training Punctuation Count: {total_punctuation_count_train}')
print(f'Total Label Punctuation Count: {total_punctuation_count_label}')

Total Training Punctuation Count: 3608886
Total Label Punctuation Count: 115670


### Normalize by removing all punctuations

In [8]:

replace_punc = lambda x: ''.join([' ' if ch in punctuations else ch for ch in x])
train_inputs.iloc[:, 0] = train_inputs.iloc[:, 0].apply(replace_punc)
train_labels.iloc[:, 0] = train_labels.iloc[:, 0].apply(replace_punc)


In [9]:
# Add new column with punctuation counts for each sentence
train_inputs['Punctuation_Counts_after'] = train_inputs[0].apply(count_punctuations)
train_labels['Punctuation_Counts_after'] = train_labels[0].apply(count_punctuations)

# Calculate total punctuation count for all sentences in DataFrame
total_punctuation_count_train = train_inputs['Punctuation_Counts_after'].sum()
total_punctuation_count_label = train_labels['Punctuation_Counts_after'].sum()


# Print total punctuation count
print(f'Total Training Punctuation Count: {total_punctuation_count_train}')
print(f'Total Label Punctuation Count: {total_punctuation_count_label}')

Total Training Punctuation Count: 0
Total Label Punctuation Count: 0


In [10]:
#Drop columns to avoid confusion
train_inputs.drop('Punctuation_Counts_after', axis=1, inplace=True)
train_labels.drop('Punctuation_Counts_after', axis=1, inplace=True)


### We notice that there is an inconsistent use of 'ة' and 'ه' at the end of the words. The same goes with the use of 'ي' and 'ى'.
### Thus, we need to normalize by replacing 'ة'' with 'ه' and 'ى' with 'ي'

In [11]:
replace_ha2_marboota = lambda x: ''.join(['ه' if ch == 'ة' else ch for ch in x])
replace_ya2 = lambda x: ''.join(['ي' if ch == 'ى' else ch for ch in x])
train_inputs.iloc[:,0] = train_inputs.iloc[:,0].apply(replace_ha2_marboota)
train_labels.iloc[:,0] = train_labels.iloc[:,0].apply(replace_ha2_marboota)
train_inputs.iloc[:,0] = train_inputs.iloc[:,0].apply(replace_ya2)
train_labels.iloc[:,0] = train_labels.iloc[:,0].apply(replace_ya2)


In [12]:
print(train_inputs[0][0])
print(train_labels[0][0])

وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينوف  قد أمر بسحب جميع القوات الأوكرانيه من القرم   وسيطرت قوات روسيه صباح الاثنين علي قاعده بحريه أوكرانيه في فيودوسيا  في ثالث هجوم من نوعه خلال 48 ساعه  وذلك بحسب تصريحات مسؤولين أوكرانيين لبي بي سي    وقال المتحدث باسم وزاره الدفاع الأوكرانيه فلاديسلاف سيليزنيوف إن القوات الروسيه هاجمت القاعده وألقت القبض علي الجنود الأوكرانيين في قاعده فيودوسيا وقيدت أيادي ضباطهم   ومن المتوقع أن تسيطر الأزمه الأوكرانيه علي قمه مجموعه الدول الصناعيه السبع في لاهاي   مواضيع قد تهمك نهايه  وأكد الرئيس الأمريكي باراك أوباما خلال لقاء مع نظيره الصيني شي جين بينغ علي أن  واشنطن وبكين يمكنهما  بالعمل سويا  تعزيز القانون الدولي واحترام سياده الدول    وتسيطر قوات روسيه حاليا علي معظم القواعد العسكريه الأوكرانيه في القرم التي أعلنت موسكو ضمها للاتحاد الروسي بعد استفتاء أجرته السلطات المحليه هناك   قلق بالغ  وقال مارك لوين  مراسل بي بي سي في القرم  إن القوات الروسيه تسيطر بشكل كامل علي القاعده  ونقلت الجنود الأوكرانيين بعيدا إلي مكان مجهول   وتعد قاعده فيودوسيا واح

### We notice how the word 'الأوكرانية' was normalized to 'الأوكرانيه'

In [13]:
train_inputs[0]

0        وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...
1        بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...
2        وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...
3        ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...
4        مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...
                               ...                        
37514    يثور بركان بولسكي تولباشيك شرقي روسيا منذ نوفم...
37515    بينما احتدمت أزمه احتجاز الرهائن علي يد لاجئ إ...
37516    رمضان آخر يستقبله المسلمون في ظل كورونا  للعام...
37517    بعض الأصوات المؤيده للنظم العربيه استغلت اقتحا...
37518    تزامنا مع الذكري التسعين لاكتشاف مقبره توت عنخ...
Name: 0, Length: 37519, dtype: object

### Analyze by check if the text has any diacritics, If so normalize by removing them

In [14]:

# Regular expression to match diacritics in Arabic text
diacritic_pattern = re.compile('[\u064B-\u065F\u0670]')

# Function to count diacritics in a given sentence
def count_diacritics(sentence):
    return len(re.findall(diacritic_pattern, sentence))

# Add new column with diacritic counts for each sentence
train_inputs['Diacritic_Counts'] = train_inputs[0].apply(count_diacritics)
train_labels['Diacritic_Counts'] = train_labels[0].apply(count_diacritics)

# Calculate total diacritic count for all sentences in DataFrame
total_train_diacritic_count = train_inputs['Diacritic_Counts'].sum()
total_label_diacritic_count = train_labels['Diacritic_Counts'].sum()


print(f'Total Training Diacritic Count: {total_train_diacritic_count}')
print(f'Total Lebels Diacritic Count: {total_label_diacritic_count}')



Total Training Diacritic Count: 152867
Total Lebels Diacritic Count: 5966


### After analyzing, we notice how some words in the data have diacritics and some do not. Hence, we need to normalize by removing all diacritics and non-arabic words

In [15]:
# Define a regular expression to match diacritics
diacritics_pattern = re.compile("[ًٌٍَُِّْ]")

# Define a regular expression to match non-Arabic characters
non_arabic_pattern = re.compile("[^\u0600-\u06FF ]")

# Define a function to preprocess the text data
def preprocess_text(text):
    # Remove diacritics from the text
    text = diacritics_pattern.sub("", text)

    # Remove non-Arabic characters from the text
    text = non_arabic_pattern.sub("", text)

    # Remove Arabic punctuations from the text
    text = ''.join([' ' if ch in punctuations else ch for ch in text])

    return text

# Preprocess the input data
train_inputs['cleaned_text'] = train_inputs[0].apply(preprocess_text)
train_labels['cleaned_text'] = train_labels[0].apply(preprocess_text)

In [16]:
# Calculate total diacritic count for all sentences in DataFrame
total_train_diacritic_count = train_inputs['cleaned_text'].apply(count_diacritics).sum()
total_label_diacritic_count = train_labels['cleaned_text'].apply(count_diacritics).sum()


print(f'Total Training Diacritic Count: {total_train_diacritic_count}')
print(f'Total Labels Diacritic Count: {total_label_diacritic_count}')

Total Training Diacritic Count: 0
Total Labels Diacritic Count: 0


In [17]:
#rename original text column to avoid confusion
train_inputs = train_inputs.rename(columns={0: 'original_Text'})
train_labels = train_labels.rename(columns={0: 'original_Text'})
train_inputs.head()

original_Text  \
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...   
1  بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...   
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...   
3  ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...   
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...   

   Punctuation_Counts_before  Diacritic_Counts  \
0                        125                 0   
1                         70                 1   
2                         35                 0   
3                        284                15   
4                         25                 3   

                                        cleaned_text  
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...  
1  بحلول عام  ستحتاج مصر إلي  مليار متر مكعب فوق ...  
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...  
3  ووقع اختياره علي واد عمقه  متر محاط بثماني قمم...  
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...

In [18]:
all_text = ' '.join(train_inputs['cleaned_text'])

# Split the string into words and get the unique words
unique_words = set(all_text.split())

# Print the unique words
print(unique_words)

{'لتدع', 'وجعلتها', 'لحزبهم', 'سريناغار', 'وشبابه', 'تأخرهم', 'تستأصل', 'وانفراجات', 'وفيغولي', 'استحقت', 'فيرهيل', 'الطاحن', 'وحزينون', 'سيؤخر', 'وأجهزتنا', 'ماندابام', 'باكيتا', 'ستيكس', 'بالشكر', 'وكلامها', 'لتخليق', 'ويشربون', 'بنسق', 'مقامر', 'لمنفاها', 'المحتملين', 'بالتزود', 'وكرسه', 'ماكرين', 'بالشهيد', 'الطفيليه', 'اعتيادا', 'المتلهفين', 'ومستوطنا', 'جوام', 'آدامي', 'بأعضاء', 'ليتخذوا', 'وتشبعه', 'وتحفزنا', 'بـنشر', 'وبأمكانكم', 'غالانيس', 'خوذا', 'لأمر', 'تشرتشل', 'لايمكن', 'وبحمض', 'خنافس', 'ومروه', 'لترشح', 'بأنفسكن', 'والمدعي', 'للتساهل', 'ومحرومه', 'بالغوريلا', 'احتمالاتها', 'نيته', 'لمراستلها', 'وأقليات', 'الالتواءات', 'هيلثبالك', 'جويدغفوندن', 'لمصاعب', 'الرواندي', 'راجندر', 'والجوارح', 'متفاءله', 'المتساقطه', 'والمداخلات', 'تستطيل', 'المرير', 'ويطوق', 'فسيأخذون', 'ليرا', 'جاربين', 'والتخصصات', 'سلحت', 'قطبيا', 'لنعيها', 'والزقايق', 'أتخذوا', 'وإغواؤهن', 'استثمر', 'فتتماشي', 'اكتئابا', 'نوافذه', 'متخمه', 'للانحراف', 'فاندنبرغ', 'يخطئن', 'وشاباته', 'وولبيرغ', 'مرافقوه', 

In [19]:
print(len(list(unique_words)))

337948


In [20]:
train_inputs.head()

original_Text  \
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...   
1  بحلول عام 2050 ستحتاج مصر إلي 21 مليار متر مكع...   
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...   
3  ووقع اختياره علي واد عمقه 800 متر محاط بثماني ...   
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...   

   Punctuation_Counts_before  Diacritic_Counts  \
0                        125                 0   
1                         70                 1   
2                         35                 0   
3                        284                15   
4                         25                 3   

                                        cleaned_text  
0  وكان الرئيس الأوكراني المؤقت  الكسندر تورتشينو...  
1  بحلول عام  ستحتاج مصر إلي  مليار متر مكعب فوق ...  
2  وذكرت وكاله الأنباء المحليه  جي إن إس  أن جماع...  
3  ووقع اختياره علي واد عمقه  متر محاط بثماني قمم...  
4  مسلح حوثي في إب  وقال المصدر إن المسلحين الحوث...

## Text Tokenization

In [21]:
nltk.download('punkt')
# Define a function to tokenize the text data
def tokenize(text):
    # Tokenize the text using the Arabic word tokenizer from the nltk library
    tokens = nltk.word_tokenize(text)

    # Split any multi-word tokens into separate tokens
    new_tokens = []
    for token in tokens:
        if ' ' in token:
            subtokens = nltk.word_tokenize(token)
            new_tokens.extend(subtokens)
        else:
            new_tokens.append(token)
    return new_tokens
# train_inputs_labels = pd.DataFrame([])
train_inputs['tokens'] = train_inputs['cleaned_text'].apply(tokenize)
train_labels['tokens'] = train_labels['cleaned_text'].apply(tokenize)




[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [22]:
train_labels.head()

original_Text  \
0  بدأت القوات الأوكرانيه الانسحاب من شبه جزيره ا...   
1   هل سيتم تغيير العباره الشهيره للمؤرخ اليوناني...   
2  قالت الشرطه في القطاع الهندي من إقليم كشمير إن...   
3  في عام 816  تجول راهب يدعي كوكاي  في المنحدرات...   
4  أكد مصدر في  الحراك التهامي  لأبناء محافظه الح...   

   Punctuation_Counts_before  Diacritic_Counts  \
0                          3                 0   
1                          7                 0   
2                          2                 0   
3                          6                 0   
4                          3                 0   

                                        cleaned_text  \
0  بدأت القوات الأوكرانيه الانسحاب من شبه جزيره ا...   
1   هل سيتم تغيير العباره الشهيره للمؤرخ اليوناني...   
2  قالت الشرطه في القطاع الهندي من إقليم كشمير إن...   
3  في عام   تجول راهب يدعي كوكاي  في المنحدرات كث...   
4  أكد مصدر في  الحراك التهامي  لأبناء محافظه الح...   

                                              tokens  
0  [بدأت, القوات, الأوكرانيه, الانسحاب, من, شبه, ...  
1  [هل, سيتم, تغيير, العباره, الشهيره, للمؤرخ, ال...  
2  [قالت, الشرطه, في, القطاع, الهندي, من, إقليم, ...  
3  [في, عام, تجول, راهب, يدعي, كوكاي, في, المنحدر...  
4  [أكد, مصدر, في, الحراك, التهامي, لأبناء, محافظ...

In [23]:
# Get the unique tokens in all articles
unique_tokens = pd.Series(train_inputs['tokens'].explode().unique())

# Preview the unique tokens
print(unique_tokens)

0              وكان
1            الرئيس
2         الأوكراني
3            المؤقت
4           الكسندر
            ...    
337943      للتنفير
337944        تأبيد
337945       لايؤشر
337946     هيلتوفير
337947        فكتوم
Length: 337948, dtype: object


## Removing stop words

### We will remove stop words to ease the training process

In [24]:

stop_words = set(stopwords.words('arabic'))
def remove_stop_words(tokens):
    filtered_tokens = [token for token in tokens if token not in stop_words]
    return filtered_tokens
train_inputs['tokens'] = train_inputs['tokens'].apply(remove_stop_words)

In [25]:
# Get the unique tokens in all articles
unique_tokens = pd.Series(train_inputs['tokens'].explode().unique())

# Preview the unique tokens
print(unique_tokens)

0              وكان
1            الرئيس
2         الأوكراني
3            المؤقت
4           الكسندر
            ...    
337460      للتنفير
337461        تأبيد
337462       لايؤشر
337463     هيلتوفير
337464        فكتوم
Length: 337465, dtype: object


### Note how the number of unique tokens in the training data was reduced from 337947 before removing stop words to 337464 after removing stop words

In [26]:
# from nltk.stem.isri import ISRIStemmer
# # Create an instance of the ISRI Arabic stemmer
# stemmer = ISRIStemmer()

# # Define a function to apply stemming to a list of tokens
# def stem_tokens(tokens):
#     stemmed_tokens = []
#     for token in tokens:
#         stemmed_token = stemmer.stem(token)
#         stemmed_tokens.append(stemmed_token)
#     return stemmed_tokens

# train_inputs['stemmed_tokens'] = train_inputs['tokens'].apply(stem_tokens)


## Lemmatizing tokens

In [27]:
from nltk.stem.isri import ISRIStemmer
def lemmatize_tokens(tokens):
    lemmatized_tokens = []
    for token in tokens:
        lemmatized_token = ISRIStemmer().suf32(token)
        lemmatized_tokens.append(lemmatized_token)
    return lemmatized_tokens

train_inputs['lemmatized_tokens'] = train_inputs['tokens'].apply(lemmatize_tokens)


In [28]:
train_inputs['lemmatized_tokens'][2]

['وذكرت',
 'وكاله',
 'الأنباء',
 'المحليه',
 'جي',
 'إس',
 'جماعه',
 'جيش',
 'محمد',
 'المتشدده',
 'أعلنت',
 'مسؤوليت',
 'الهجوم',
 'منطقه',
 'كشمير',
 'المتنازع',
 'علي',
 'الهند',
 'وباكس',
 'خلال',
 'العقود',
 'الست',
 'الماضيه',
 'ظلت',
 'منطقه',
 'كشمير',
 'القريبه',
 'جبال',
 'الهيمالا',
 'محل',
 'نزاع',
 'الهند',
 'وباكس',
 'الجنه',
 'الملعونه',
 'دموع',
 'الفقراء',
 'كشمير',
 'لماذا',
 'يلجأ',
 'الناس',
 'إلي',
 'أضرحه',
 'الصوفي',
 'كشمير',
 'الهنديه',
 'بالصور',
 'الطفوله',
 'المسروقه',
 'كشمير',
 'فمنذ',
 'تقسيم',
 'الهند',
 'وقيام',
 'باكس',
 'عام',
 'وقعت',
 'حرب',
 'البلد',
 'حول',
 'منطقه',
 'كشمير',
 'الأغلبيه',
 'المسلمه',
 'والتي',
 'يطالب',
 'البلد',
 'بالسياده',
 'علي',
 'وتعد',
 'كشمير',
 'اليوم',
 'واحده',
 'المناطق',
 'المدججه',
 'بالسلاح',
 'العالم',
 'تدير',
 'الص',
 'أجزاء',
 'الإقليم',
 'تسلسل',
 'زمني',
 'لأهم',
 'الأحداث',
 'كشمير']

## Load BERT Arabic for words embeddings

In [29]:
from transformers import AutoTokenizer, AutoModel

# load pre-trained tokenizer and model for Arabic
tokenizer = AutoTokenizer.from_pretrained("asafaya/bert-base-arabic")
model = AutoModel.from_pretrained("asafaya/bert-base-arabic")

# get embeddings for each token
tokens = ['هذا', 'هو', 'بيت', 'و', 'ذهب', 'إلى', 'سوق']
inputs = tokenizer(tokens, return_tensors="pt", padding=True, truncation=True)
outputs = model(**inputs)

embeddings = outputs.last_hidden_state.mean(dim=1).detach()

print(embeddings.tolist())


C:\Users\DELL\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.10_qbz5n2kfra8p0\LocalCache\local-packages\Python310\site-packages\torch\serialization.py:953: UserWarning: Failed to initialize NumPy: module compiled against API version 0x10 but this version of numpy is 0xf (Triggered internally at ..\torch\csrc\utils\tensor_numpy.cpp:77.)
  obj = cast(Storage, torch.UntypedStorage(nbytes))
Some weights of the model checkpoint at asafaya/bert-base-arabic were not used when initializing BertModel: ['cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
-

[[0.31527161598205566, -0.4399240016937256, -0.17854495346546173, 0.5780287981033325, 0.8602509498596191, 0.7949953675270081, 0.056156497448682785, 0.026680657640099525, -1.6595726013183594, 0.28472813963890076, 0.4051208794116974, 0.7264513373374939, 0.616670548915863, -0.09570588916540146, -2.0323543548583984, 1.4384961128234863, 0.6880986094474792, 0.06987679749727249, 0.32801297307014465, 0.5569186210632324, 0.40191566944122314, 0.2905631959438324, -0.32907986640930176, 0.08926656097173691, -1.097656488418579, -1.4114489555358887, 0.22717435657978058, 0.5248251557350159, -0.011796936392784119, -0.33999860286712646, -0.6185222864151001, -0.9222474694252014, 0.4354466497898102, -0.12227266281843185, -0.6425198912620544, -0.04567861184477806, -0.8357886672019958, 1.1150726079940796, 0.100433848798275, 0.33938291668891907, 0.5445860624313354, -1.6509555578231812, 0.003801026614382863, -0.5854602456092834, -1.6287966966629028, 0.44370603561401367, -0.6604392528533936, 1.867529273033142,

In [30]:
# def generate_embeddings(tokens):
#     embeddings = []
#     inputs = tokenizer(tokens, return_tensors="pt", padding=True, truncation=True)
#     outputs = model(**inputs)
#     embeddings = outputs.last_hidden_state.mean(dim=1).detach()
#     return embeddings.tolist()

# train_inputs['embeddings'] = train_inputs['lemmatized_tokens'].apply(generate_embeddings)

## Model Architecture
1-An Embedding layer: We need to map the input tokens into word embeddings that the model can understand. <br>
2-An Encoder: this encoder should consist of multiple multi-head attention layers to make use of the attention mechanism and positional encoding to capture the context of the words. <br>
3-Feed-forward layer: This layer should help the model extract features and learn complex non linear. <br>
4-Output Layer: This layer takes the output of the decoder layers and generates the final summary. <br>

AraBART is a useful pretrained model that we can use and fine-tune to the summarization task as it already has the above needed layers. Each layer in AraBART is useful for text summarization in different ways:

1-Input Embedding Layer: The input embedding layer in AraBART converts each token in the input sequence to an embedding vector. This layer is useful for text summarization because it allows the model to represent each token in the input sequence in a high-dimensional space.<br>

2-Multi-Head Attention Layers: AraBART has 12 multi-head attention layers, each of which computes attention weights between the input tokens. This layer is useful for text summarization because it allows the model to focus on the most relevant parts of the input sequence when generating a summary. <br>

3-Feedforward Layers: AraBART has 12 feedforward layers, each of which applies a non-linear transformation to the outputs of the multi-head attention layer. This layer is useful for text summarization because it allows the model to learn complex, non-linear relationships between the input tokens. <br>

4-Pooling Layer: The pooling layer in AraBART aggregates the contextualized representations of each token in the input sequence into a fixed-length vector. This layer is useful for text summarization because it allows the model to generate a summary of a fixed length, regardless of the length of the input sequence. <br>

5-Output Layer: The output layer in AraBART consists of a linear layer followed by a softmax activation function. This layer is useful for text summarization because it allows the model to generate a probability distribution over the tokens in the vocabulary, which can be used to generate a summary. <br>


In [ ]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

model_name = "moussaKam/AraBART"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)


In [32]:
# Convert train_inputs to list of strings
train_inputs_list = [ ' '.join(tokens) for tokens in train_inputs['tokens'].tolist() ]

# Convert train_labels to list of strings
train_labels_list = [ ' '.join(tokens) for tokens in train_labels['tokens'].tolist() ]

# Tokenize inputs and labels
train_encodings = tokenizer(train_inputs_list, truncation=True, padding=True)
train_labels_encodings = tokenizer(train_labels_list, truncation=True, padding=True)


Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


: 

: 